In [1]:
import pandas as pd
import scipy.stats as stats

from sklearn import metrics, model_selection
from catboost import CatBoostClassifier

In [2]:
df_train_mean_encoding = pd.read_csv('../../Feature_Encoding/data/train_mean_encoding.csv')
df_test_mean_encoding = pd.read_csv('../../Feature_Encoding/data/test_mean_encoding.csv')
train = pd.read_csv('../../Feature_Engineering/data/other-cleaned_train.csv')

In [3]:
def cross_val(model, x_train, y_train):
    score_cross_val = model_selection.cross_val_score(model, x_train, y_train, cv=5)
    print(score_cross_val.mean())

In [4]:
#Realiza busqueda completa combinando los parametros
def catboost(x_train, y_train, x_validation, y_validation):
    catb_classifier = CatBoostClassifier()
    params_catb = {'n_estimators': [50, 100, 200], 'learning_rate': [0.01, 0.05, 0.1], 'l2_leaf_reg': [0, 1, 5]}    
    catb_gs = model_selection.GridSearchCV(catb_classifier, params_catb, cv=5)
    catb_gs.fit(x_train, y_train)
    catb_best = catb_gs.best_estimator_
    print(catb_gs.best_params_)
    print('catb: {}'.format(catb_best.score(x_validation, y_validation)))
    return catb_best

In [5]:
#Realiza busqueda random dentro de los parametros validos
def catboost2(x_train, y_train, x_validation, y_validation):
    catb_classifier = CatBoostClassifier()
    params_catb_2={
        'n_estimators':stats.randint(10,500),'learning_rate':stats.uniform(0.01,0.3),
        'subsample':stats.uniform(0.3,0.7),'l2_leaf_reg':[1,5,10],
        'max_depth':[3,10,6],'colsample_bylevel':stats.uniform(0.,0.6)
    }
    
    catb_rs = model_selection.RandomizedSearchCV(CatBoostClassifier(),
                          param_distributions=params_catb_2,
                          cv=2,
                          scoring='neg_log_loss',
                          verbose=1,
                          n_iter=200)
    
    catb_rs.fit(x_train, y_train)
    catb_best = catb_rs.best_estimator_
    print(catb_rs.best_params_)
    print('catb: {}'.format(catb_best.score(x_validation, y_validation)))
    return catb_best

In [6]:
def test_model(model, x_test, y_test):
    predictions = model.predict_proba(x_test)[:,1]
    logloss = metrics.log_loss(y_test, predictions)
    accuracy = metrics.accuracy_score(y_test, predictions.round())
    print("Accuracy: %.2f%%, Logloss: %.2f" % (accuracy*100.0, logloss))

In [7]:
y = train.Target
x_train_mean_encoding, x_validation_mean_encoding, y_train_mean_encoding, y_validation_mean_encoding = model_selection.train_test_split(df_train_mean_encoding, y, test_size=0.3, stratify=y)

## Mean encoding

In [8]:
catboost_mean_encoding = catboost(x_train_mean_encoding, y_train_mean_encoding, x_validation_mean_encoding, y_validation_mean_encoding)
test_model(catboost_mean_encoding,x_validation_mean_encoding,y_validation_mean_encoding)
cross_val(catboost_mean_encoding, x_train_mean_encoding, y_train_mean_encoding)

0:	learn: 0.6826295	total: 217ms	remaining: 10.6s
1:	learn: 0.6724637	total: 232ms	remaining: 5.57s
2:	learn: 0.6633149	total: 242ms	remaining: 3.78s
3:	learn: 0.6538243	total: 248ms	remaining: 2.85s
4:	learn: 0.6456483	total: 254ms	remaining: 2.29s
5:	learn: 0.6360605	total: 261ms	remaining: 1.92s
6:	learn: 0.6289203	total: 274ms	remaining: 1.68s
7:	learn: 0.6208873	total: 284ms	remaining: 1.49s
8:	learn: 0.6130313	total: 290ms	remaining: 1.32s
9:	learn: 0.6050413	total: 296ms	remaining: 1.19s
10:	learn: 0.5963903	total: 305ms	remaining: 1.08s
11:	learn: 0.5883124	total: 311ms	remaining: 985ms
12:	learn: 0.5801141	total: 317ms	remaining: 903ms
13:	learn: 0.5718911	total: 324ms	remaining: 833ms
14:	learn: 0.5653315	total: 332ms	remaining: 775ms
15:	learn: 0.5602490	total: 338ms	remaining: 719ms
16:	learn: 0.5546335	total: 344ms	remaining: 668ms
17:	learn: 0.5477501	total: 350ms	remaining: 622ms
18:	learn: 0.5411056	total: 356ms	remaining: 581ms
19:	learn: 0.5364796	total: 362ms	remaini

19:	learn: 0.5393204	total: 226ms	remaining: 339ms
20:	learn: 0.5344879	total: 232ms	remaining: 321ms
21:	learn: 0.5292368	total: 238ms	remaining: 303ms
22:	learn: 0.5238214	total: 244ms	remaining: 286ms
23:	learn: 0.5194129	total: 250ms	remaining: 271ms
24:	learn: 0.5138139	total: 256ms	remaining: 256ms
25:	learn: 0.5096160	total: 262ms	remaining: 242ms
26:	learn: 0.5053229	total: 268ms	remaining: 228ms
27:	learn: 0.4999939	total: 274ms	remaining: 216ms
28:	learn: 0.4960945	total: 281ms	remaining: 204ms
29:	learn: 0.4917680	total: 288ms	remaining: 192ms
30:	learn: 0.4880752	total: 293ms	remaining: 180ms
31:	learn: 0.4834362	total: 305ms	remaining: 171ms
32:	learn: 0.4790745	total: 311ms	remaining: 160ms
33:	learn: 0.4759956	total: 317ms	remaining: 149ms
34:	learn: 0.4728663	total: 323ms	remaining: 139ms
35:	learn: 0.4694827	total: 329ms	remaining: 128ms
36:	learn: 0.4662752	total: 336ms	remaining: 118ms
37:	learn: 0.4622020	total: 342ms	remaining: 108ms
38:	learn: 0.4584312	total: 348

83:	learn: 0.3541242	total: 628ms	remaining: 120ms
84:	learn: 0.3529650	total: 634ms	remaining: 112ms
85:	learn: 0.3516175	total: 640ms	remaining: 104ms
86:	learn: 0.3501370	total: 653ms	remaining: 97.6ms
87:	learn: 0.3490713	total: 658ms	remaining: 89.8ms
88:	learn: 0.3473671	total: 664ms	remaining: 82ms
89:	learn: 0.3463645	total: 669ms	remaining: 74.4ms
90:	learn: 0.3451425	total: 677ms	remaining: 66.9ms
91:	learn: 0.3435946	total: 684ms	remaining: 59.5ms
92:	learn: 0.3423116	total: 692ms	remaining: 52.1ms
93:	learn: 0.3411281	total: 700ms	remaining: 44.7ms
94:	learn: 0.3399348	total: 710ms	remaining: 37.4ms
95:	learn: 0.3387964	total: 718ms	remaining: 29.9ms
96:	learn: 0.3376644	total: 740ms	remaining: 22.9ms
97:	learn: 0.3367493	total: 755ms	remaining: 15.4ms
98:	learn: 0.3359499	total: 762ms	remaining: 7.69ms
99:	learn: 0.3346860	total: 767ms	remaining: 0us
0:	learn: 0.6827056	total: 14.7ms	remaining: 1.45s
1:	learn: 0.6725771	total: 20.8ms	remaining: 1.02s
2:	learn: 0.6634849	to

57:	learn: 0.3960818	total: 433ms	remaining: 314ms
58:	learn: 0.3934817	total: 439ms	remaining: 305ms
59:	learn: 0.3913903	total: 444ms	remaining: 296ms
60:	learn: 0.3896666	total: 450ms	remaining: 288ms
61:	learn: 0.3875830	total: 455ms	remaining: 279ms
62:	learn: 0.3857480	total: 461ms	remaining: 271ms
63:	learn: 0.3841961	total: 466ms	remaining: 262ms
64:	learn: 0.3826268	total: 472ms	remaining: 254ms
65:	learn: 0.3807388	total: 478ms	remaining: 246ms
66:	learn: 0.3788425	total: 484ms	remaining: 238ms
67:	learn: 0.3775125	total: 489ms	remaining: 230ms
68:	learn: 0.3758654	total: 495ms	remaining: 222ms
69:	learn: 0.3741832	total: 500ms	remaining: 214ms
70:	learn: 0.3728259	total: 506ms	remaining: 207ms
71:	learn: 0.3708021	total: 511ms	remaining: 199ms
72:	learn: 0.3692129	total: 519ms	remaining: 192ms
73:	learn: 0.3674831	total: 526ms	remaining: 185ms
74:	learn: 0.3654843	total: 533ms	remaining: 178ms
75:	learn: 0.3639175	total: 538ms	remaining: 170ms
76:	learn: 0.3624780	total: 544

23:	learn: 0.5138139	total: 219ms	remaining: 692ms
24:	learn: 0.5081215	total: 225ms	remaining: 674ms
25:	learn: 0.5032596	total: 233ms	remaining: 664ms
26:	learn: 0.4981870	total: 240ms	remaining: 648ms
27:	learn: 0.4920055	total: 245ms	remaining: 631ms
28:	learn: 0.4880452	total: 251ms	remaining: 615ms
29:	learn: 0.4837358	total: 257ms	remaining: 600ms
30:	learn: 0.4797850	total: 263ms	remaining: 585ms
31:	learn: 0.4749533	total: 268ms	remaining: 570ms
32:	learn: 0.4704621	total: 274ms	remaining: 556ms
33:	learn: 0.4675131	total: 279ms	remaining: 542ms
34:	learn: 0.4640767	total: 285ms	remaining: 530ms
35:	learn: 0.4604379	total: 291ms	remaining: 517ms
36:	learn: 0.4576001	total: 297ms	remaining: 505ms
37:	learn: 0.4534138	total: 302ms	remaining: 493ms
38:	learn: 0.4495171	total: 308ms	remaining: 481ms
39:	learn: 0.4466315	total: 313ms	remaining: 470ms
40:	learn: 0.4437472	total: 319ms	remaining: 458ms
41:	learn: 0.4397301	total: 324ms	remaining: 448ms
42:	learn: 0.4369157	total: 330

...

48:	learn: 0.2161662	total: 423ms	remaining: 1.3s
49:	learn: 0.2145967	total: 431ms	remaining: 1.29s
50:	learn: 0.2139487	total: 439ms	remaining: 1.28s
51:	learn: 0.2127407	total: 448ms	remaining: 1.28s
52:	learn: 0.2111663	total: 457ms	remaining: 1.27s
53:	learn: 0.2100919	total: 466ms	remaining: 1.26s
54:	learn: 0.2090213	total: 476ms	remaining: 1.25s
55:	learn: 0.2070333	total: 484ms	remaining: 1.25s
56:	learn: 0.2060129	total: 493ms	remaining: 1.24s
57:	learn: 0.2042665	total: 503ms	remaining: 1.23s
58:	learn: 0.2029291	total: 512ms	remaining: 1.22s
59:	learn: 0.2016132	total: 520ms	remaining: 1.21s
60:	learn: 0.2006468	total: 530ms	remaining: 1.21s
61:	learn: 0.1999046	total: 539ms	remaining: 1.2s
62:	learn: 0.1988507	total: 547ms	remaining: 1.19s
63:	learn: 0.1972324	total: 555ms	remaining: 1.18s
64:	learn: 0.1963612	total: 564ms	remaining: 1.17s
65:	learn: 0.1946900	total: 572ms	remaining: 1.16s
66:	learn: 0.1933908	total: 582ms	remaining: 1.16s
67:	learn: 0.1924152	total: 590ms

23:	learn: 0.2617249	total: 215ms	remaining: 1.58s
24:	learn: 0.2596107	total: 223ms	remaining: 1.56s
25:	learn: 0.2557719	total: 233ms	remaining: 1.56s
26:	learn: 0.2535554	total: 243ms	remaining: 1.56s
27:	learn: 0.2511000	total: 252ms	remaining: 1.54s
28:	learn: 0.2489373	total: 261ms	remaining: 1.54s
29:	learn: 0.2477812	total: 269ms	remaining: 1.52s
30:	learn: 0.2455182	total: 277ms	remaining: 1.51s
31:	learn: 0.2438927	total: 287ms	remaining: 1.5s
32:	learn: 0.2410065	total: 295ms	remaining: 1.49s
33:	learn: 0.2394744	total: 304ms	remaining: 1.48s
34:	learn: 0.2383278	total: 313ms	remaining: 1.48s
35:	learn: 0.2356502	total: 326ms	remaining: 1.48s
36:	learn: 0.2340546	total: 337ms	remaining: 1.48s
37:	learn: 0.2315078	total: 348ms	remaining: 1.48s
38:	learn: 0.2302682	total: 356ms	remaining: 1.47s
39:	learn: 0.2286441	total: 366ms	remaining: 1.46s
40:	learn: 0.2264911	total: 379ms	remaining: 1.47s
41:	learn: 0.2249368	total: 387ms	remaining: 1.46s
42:	learn: 0.2236983	total: 398m

194:	learn: 0.0916136	total: 1.82s	remaining: 46.8ms
195:	learn: 0.0910610	total: 1.83s	remaining: 37.4ms
196:	learn: 0.0906617	total: 1.84s	remaining: 28.1ms
197:	learn: 0.0901401	total: 1.85s	remaining: 18.7ms
198:	learn: 0.0897963	total: 1.86s	remaining: 9.35ms
199:	learn: 0.0892859	total: 1.87s	remaining: 0us
0:	learn: 0.6050010	total: 8.79ms	remaining: 1.75s
1:	learn: 0.5394850	total: 17ms	remaining: 1.68s
2:	learn: 0.4921439	total: 25.2ms	remaining: 1.65s
3:	learn: 0.4531532	total: 33.6ms	remaining: 1.64s
4:	learn: 0.4218127	total: 41.8ms	remaining: 1.63s
5:	learn: 0.3979123	total: 50.6ms	remaining: 1.64s
6:	learn: 0.3827423	total: 59.9ms	remaining: 1.65s
7:	learn: 0.3693660	total: 67.7ms	remaining: 1.62s
8:	learn: 0.3567531	total: 75.9ms	remaining: 1.61s
9:	learn: 0.3470844	total: 83.2ms	remaining: 1.58s
10:	learn: 0.3360078	total: 91.7ms	remaining: 1.57s
11:	learn: 0.3273343	total: 99.8ms	remaining: 1.56s
12:	learn: 0.3193996	total: 110ms	remaining: 1.58s
13:	learn: 0.3144557	t

160:	learn: 0.1094512	total: 1.43s	remaining: 345ms
161:	learn: 0.1089258	total: 1.44s	remaining: 337ms
162:	learn: 0.1081270	total: 1.44s	remaining: 328ms
163:	learn: 0.1073801	total: 1.45s	remaining: 319ms
164:	learn: 0.1068616	total: 1.46s	remaining: 310ms
165:	learn: 0.1060419	total: 1.47s	remaining: 301ms
166:	learn: 0.1055611	total: 1.48s	remaining: 293ms
167:	learn: 0.1050808	total: 1.49s	remaining: 284ms
168:	learn: 0.1047149	total: 1.5s	remaining: 275ms
169:	learn: 0.1042748	total: 1.51s	remaining: 266ms
170:	learn: 0.1037751	total: 1.52s	remaining: 257ms
171:	learn: 0.1033029	total: 1.53s	remaining: 249ms
172:	learn: 0.1028510	total: 1.54s	remaining: 240ms
173:	learn: 0.1024187	total: 1.54s	remaining: 231ms
174:	learn: 0.1016523	total: 1.55s	remaining: 222ms
175:	learn: 0.1010860	total: 1.56s	remaining: 213ms
176:	learn: 0.1006390	total: 1.57s	remaining: 204ms
177:	learn: 0.1002251	total: 1.58s	remaining: 195ms
178:	learn: 0.0998290	total: 1.59s	remaining: 186ms
179:	learn: 0

131:	learn: 0.1278387	total: 1.23s	remaining: 635ms
132:	learn: 0.1268348	total: 1.25s	remaining: 630ms
133:	learn: 0.1260464	total: 1.28s	remaining: 633ms
134:	learn: 0.1254100	total: 1.32s	remaining: 634ms
135:	learn: 0.1246663	total: 1.33s	remaining: 628ms
136:	learn: 0.1238319	total: 1.35s	remaining: 620ms
137:	learn: 0.1230169	total: 1.36s	remaining: 611ms
138:	learn: 0.1220581	total: 1.38s	remaining: 603ms
139:	learn: 0.1213674	total: 1.4s	remaining: 598ms
140:	learn: 0.1202215	total: 1.4s	remaining: 587ms
141:	learn: 0.1193931	total: 1.41s	remaining: 577ms
142:	learn: 0.1185391	total: 1.42s	remaining: 567ms
143:	learn: 0.1177681	total: 1.43s	remaining: 556ms
144:	learn: 0.1169477	total: 1.44s	remaining: 546ms
145:	learn: 0.1160938	total: 1.45s	remaining: 536ms
146:	learn: 0.1150823	total: 1.46s	remaining: 525ms
147:	learn: 0.1139889	total: 1.47s	remaining: 515ms
148:	learn: 0.1135810	total: 1.48s	remaining: 505ms
149:	learn: 0.1128016	total: 1.48s	remaining: 495ms
150:	learn: 0.

In [9]:
catboost_mean_encoding = catboost2(x_train_mean_encoding, y_train_mean_encoding, x_validation_mean_encoding, y_validation_mean_encoding)
test_model(catboost_mean_encoding,x_validation_mean_encoding,y_validation_mean_encoding)
cross_val(catboost_mean_encoding, x_train_mean_encoding, y_train_mean_encoding)

Fitting 2 folds for each of 200 candidates, totalling 400 fits
0:	learn: 0.5605116	total: 34.5ms	remaining: 5.07s
1:	learn: 0.4769608	total: 60.8ms	remaining: 4.44s
2:	learn: 0.4231538	total: 86.4ms	remaining: 4.18s
3:	learn: 0.3885946	total: 116ms	remaining: 4.18s
4:	learn: 0.3541241	total: 142ms	remaining: 4.07s
5:	learn: 0.3368607	total: 171ms	remaining: 4.04s
6:	learn: 0.3146664	total: 194ms	remaining: 3.9s
7:	learn: 0.3020258	total: 218ms	remaining: 3.82s
8:	learn: 0.2916796	total: 243ms	remaining: 3.76s
9:	learn: 0.2831054	total: 270ms	remaining: 3.73s
10:	learn: 0.2716430	total: 296ms	remaining: 3.68s
11:	learn: 0.2646989	total: 324ms	remaining: 3.67s
12:	learn: 0.2592446	total: 347ms	remaining: 3.6s
13:	learn: 0.2564583	total: 352ms	remaining: 3.37s
14:	learn: 0.2505409	total: 376ms	remaining: 3.33s
15:	learn: 0.2461414	total: 405ms	remaining: 3.34s
16:	learn: 0.2422386	total: 430ms	remaining: 3.31s
17:	learn: 0.2350670	total: 457ms	remaining: 3.3s
18:	learn: 0.2256212	total: 4

17:	learn: 0.2344705	total: 428ms	remaining: 3.09s
18:	learn: 0.2300160	total: 455ms	remaining: 3.09s
19:	learn: 0.2274628	total: 497ms	remaining: 3.18s
20:	learn: 0.2220225	total: 549ms	remaining: 3.32s
21:	learn: 0.2173240	total: 587ms	remaining: 3.36s
22:	learn: 0.2120931	total: 610ms	remaining: 3.32s
23:	learn: 0.2101298	total: 639ms	remaining: 3.3s
24:	learn: 0.2076689	total: 663ms	remaining: 3.26s
25:	learn: 0.2053037	total: 687ms	remaining: 3.22s
26:	learn: 0.2024312	total: 715ms	remaining: 3.21s
27:	learn: 0.2006775	total: 736ms	remaining: 3.15s
28:	learn: 0.1970033	total: 769ms	remaining: 3.15s
29:	learn: 0.1931476	total: 795ms	remaining: 3.13s
30:	learn: 0.1898771	total: 823ms	remaining: 3.1s
31:	learn: 0.1871270	total: 853ms	remaining: 3.09s
32:	learn: 0.1851385	total: 884ms	remaining: 3.08s
33:	learn: 0.1816906	total: 916ms	remaining: 3.07s
34:	learn: 0.1792517	total: 944ms	remaining: 3.05s
35:	learn: 0.1762054	total: 970ms	remaining: 3.02s
36:	learn: 0.1741148	total: 999ms

33:	learn: 0.2572344	total: 206ms	remaining: 1.16s
34:	learn: 0.2547179	total: 210ms	remaining: 1.14s
35:	learn: 0.2527077	total: 216ms	remaining: 1.14s
36:	learn: 0.2494915	total: 222ms	remaining: 1.13s
37:	learn: 0.2474993	total: 229ms	remaining: 1.13s
38:	learn: 0.2468345	total: 234ms	remaining: 1.12s
39:	learn: 0.2450933	total: 240ms	remaining: 1.11s
40:	learn: 0.2437464	total: 245ms	remaining: 1.1s
41:	learn: 0.2425646	total: 251ms	remaining: 1.09s
42:	learn: 0.2406178	total: 257ms	remaining: 1.09s
43:	learn: 0.2391918	total: 263ms	remaining: 1.08s
44:	learn: 0.2380890	total: 268ms	remaining: 1.07s
45:	learn: 0.2365397	total: 275ms	remaining: 1.07s
46:	learn: 0.2353016	total: 282ms	remaining: 1.07s
47:	learn: 0.2342489	total: 288ms	remaining: 1.06s
48:	learn: 0.2326873	total: 294ms	remaining: 1.05s
49:	learn: 0.2320387	total: 300ms	remaining: 1.05s
50:	learn: 0.2310112	total: 305ms	remaining: 1.04s
51:	learn: 0.2299034	total: 312ms	remaining: 1.04s
52:	learn: 0.2289442	total: 318m

197:	learn: 0.1178669	total: 1.2s	remaining: 164ms
198:	learn: 0.1172437	total: 1.21s	remaining: 158ms
199:	learn: 0.1169551	total: 1.22s	remaining: 152ms
200:	learn: 0.1165669	total: 1.22s	remaining: 146ms
201:	learn: 0.1163273	total: 1.23s	remaining: 140ms
202:	learn: 0.1160792	total: 1.23s	remaining: 134ms
203:	learn: 0.1155605	total: 1.24s	remaining: 128ms
204:	learn: 0.1153109	total: 1.25s	remaining: 122ms
205:	learn: 0.1149082	total: 1.25s	remaining: 116ms
206:	learn: 0.1146687	total: 1.26s	remaining: 110ms
207:	learn: 0.1134295	total: 1.27s	remaining: 104ms
208:	learn: 0.1129700	total: 1.27s	remaining: 97.4ms
209:	learn: 0.1126844	total: 1.28s	remaining: 91.4ms
210:	learn: 0.1121483	total: 1.28s	remaining: 85.3ms
211:	learn: 0.1117580	total: 1.29s	remaining: 79.3ms
212:	learn: 0.1112580	total: 1.3s	remaining: 73.2ms
213:	learn: 0.1105363	total: 1.3s	remaining: 67.1ms
214:	learn: 0.1095831	total: 1.31s	remaining: 61ms
215:	learn: 0.1089834	total: 1.32s	remaining: 54.9ms
216:	lear

139:	learn: 0.1518714	total: 789ms	remaining: 479ms
140:	learn: 0.1517089	total: 794ms	remaining: 473ms
141:	learn: 0.1509456	total: 798ms	remaining: 466ms
142:	learn: 0.1503454	total: 801ms	remaining: 460ms
143:	learn: 0.1498642	total: 806ms	remaining: 453ms
144:	learn: 0.1489829	total: 809ms	remaining: 447ms
145:	learn: 0.1484613	total: 813ms	remaining: 440ms
146:	learn: 0.1479190	total: 817ms	remaining: 434ms
147:	learn: 0.1473608	total: 821ms	remaining: 427ms
148:	learn: 0.1469818	total: 825ms	remaining: 421ms
149:	learn: 0.1463922	total: 828ms	remaining: 414ms
150:	learn: 0.1459095	total: 832ms	remaining: 408ms
151:	learn: 0.1453855	total: 837ms	remaining: 402ms
152:	learn: 0.1449275	total: 840ms	remaining: 395ms
153:	learn: 0.1443145	total: 844ms	remaining: 389ms
154:	learn: 0.1438011	total: 848ms	remaining: 383ms
155:	learn: 0.1429899	total: 852ms	remaining: 377ms
156:	learn: 0.1424667	total: 855ms	remaining: 370ms
157:	learn: 0.1419422	total: 859ms	remaining: 364ms
158:	learn: 

...

236:	learn: 0.1053176	total: 3.38s	remaining: 1.5s
237:	learn: 0.1050831	total: 3.39s	remaining: 1.48s
238:	learn: 0.1047460	total: 3.4s	remaining: 1.46s
239:	learn: 0.1044179	total: 3.41s	remaining: 1.45s
240:	learn: 0.1042803	total: 3.45s	remaining: 1.45s
241:	learn: 0.1040232	total: 3.46s	remaining: 1.43s
242:	learn: 0.1037321	total: 3.46s	remaining: 1.41s
243:	learn: 0.1033204	total: 3.47s	remaining: 1.39s
244:	learn: 0.1030462	total: 3.48s	remaining: 1.38s
245:	learn: 0.1027773	total: 3.5s	remaining: 1.36s
246:	learn: 0.1023578	total: 3.5s	remaining: 1.35s
247:	learn: 0.1022321	total: 3.52s	remaining: 1.33s
248:	learn: 0.1018306	total: 3.54s	remaining: 1.32s
249:	learn: 0.1015253	total: 3.55s	remaining: 1.31s
250:	learn: 0.1011802	total: 3.56s	remaining: 1.29s
251:	learn: 0.1010332	total: 3.57s	remaining: 1.27s
252:	learn: 0.1007859	total: 3.58s	remaining: 1.26s
253:	learn: 0.1004132	total: 3.6s	remaining: 1.25s
254:	learn: 0.1000458	total: 3.61s	remaining: 1.23s
255:	learn: 0.099

60:	learn: 0.2265432	total: 1.02s	remaining: 4.68s
61:	learn: 0.2257024	total: 1.02s	remaining: 4.62s
62:	learn: 0.2246291	total: 1.03s	remaining: 4.58s
63:	learn: 0.2231543	total: 1.04s	remaining: 4.53s
64:	learn: 0.2218261	total: 1.05s	remaining: 4.49s
65:	learn: 0.2207669	total: 1.09s	remaining: 4.55s
66:	learn: 0.2196689	total: 1.1s	remaining: 4.51s
67:	learn: 0.2185881	total: 1.11s	remaining: 4.47s
68:	learn: 0.2169881	total: 1.13s	remaining: 4.48s
69:	learn: 0.2161155	total: 1.16s	remaining: 4.51s
70:	learn: 0.2154839	total: 1.17s	remaining: 4.46s
71:	learn: 0.2132079	total: 1.18s	remaining: 4.41s
72:	learn: 0.2123864	total: 1.19s	remaining: 4.38s
73:	learn: 0.2112350	total: 1.21s	remaining: 4.37s
74:	learn: 0.2096540	total: 1.24s	remaining: 4.43s
75:	learn: 0.2091908	total: 1.25s	remaining: 4.38s
76:	learn: 0.2076778	total: 1.27s	remaining: 4.37s
77:	learn: 0.2068860	total: 1.28s	remaining: 4.35s
78:	learn: 0.2058480	total: 1.3s	remaining: 4.34s
79:	learn: 0.2052427	total: 1.32s

233:	learn: 0.1079138	total: 3.17s	remaining: 1.47s
234:	learn: 0.1075709	total: 3.18s	remaining: 1.45s
235:	learn: 0.1073395	total: 3.19s	remaining: 1.43s
236:	learn: 0.1069077	total: 3.19s	remaining: 1.41s
237:	learn: 0.1065469	total: 3.19s	remaining: 1.4s
238:	learn: 0.1063006	total: 3.2s	remaining: 1.38s
239:	learn: 0.1060116	total: 3.21s	remaining: 1.36s
240:	learn: 0.1057041	total: 3.21s	remaining: 1.35s
241:	learn: 0.1053657	total: 3.22s	remaining: 1.33s
242:	learn: 0.1050613	total: 3.22s	remaining: 1.31s
243:	learn: 0.1046297	total: 3.23s	remaining: 1.3s
244:	learn: 0.1043113	total: 3.23s	remaining: 1.28s
245:	learn: 0.1038428	total: 3.24s	remaining: 1.26s
246:	learn: 0.1035160	total: 3.24s	remaining: 1.25s
247:	learn: 0.1031894	total: 3.25s	remaining: 1.23s
248:	learn: 0.1028640	total: 3.25s	remaining: 1.21s
249:	learn: 0.1025896	total: 3.26s	remaining: 1.2s
250:	learn: 0.1022131	total: 3.26s	remaining: 1.18s
251:	learn: 0.1016409	total: 3.27s	remaining: 1.17s
252:	learn: 0.10

72:	learn: 0.2046274	total: 614ms	remaining: 2.26s
73:	learn: 0.2035900	total: 625ms	remaining: 2.26s
74:	learn: 0.2024415	total: 635ms	remaining: 2.26s
75:	learn: 0.2014284	total: 642ms	remaining: 2.25s
76:	learn: 0.2006147	total: 649ms	remaining: 2.23s
77:	learn: 0.2000436	total: 659ms	remaining: 2.23s
78:	learn: 0.1990493	total: 672ms	remaining: 2.24s
79:	learn: 0.1976439	total: 683ms	remaining: 2.24s
80:	learn: 0.1962421	total: 692ms	remaining: 2.23s
81:	learn: 0.1954751	total: 699ms	remaining: 2.22s
82:	learn: 0.1945688	total: 707ms	remaining: 2.21s
83:	learn: 0.1936943	total: 718ms	remaining: 2.21s
84:	learn: 0.1930542	total: 726ms	remaining: 2.2s
85:	learn: 0.1921202	total: 735ms	remaining: 2.19s
86:	learn: 0.1908850	total: 745ms	remaining: 2.18s
87:	learn: 0.1898890	total: 757ms	remaining: 2.19s
88:	learn: 0.1891561	total: 766ms	remaining: 2.18s
89:	learn: 0.1880669	total: 781ms	remaining: 2.19s
90:	learn: 0.1872067	total: 790ms	remaining: 2.18s
91:	learn: 0.1861253	total: 797m

253:	learn: 0.0964365	total: 2.01s	remaining: 697ms
254:	learn: 0.0962289	total: 2.02s	remaining: 688ms
255:	learn: 0.0959124	total: 2.02s	remaining: 680ms
256:	learn: 0.0955480	total: 2.03s	remaining: 672ms
257:	learn: 0.0952707	total: 2.04s	remaining: 664ms
258:	learn: 0.0950370	total: 2.05s	remaining: 656ms
259:	learn: 0.0945348	total: 2.05s	remaining: 648ms
260:	learn: 0.0942286	total: 2.06s	remaining: 640ms
261:	learn: 0.0938185	total: 2.07s	remaining: 632ms
262:	learn: 0.0934455	total: 2.08s	remaining: 624ms
263:	learn: 0.0930689	total: 2.09s	remaining: 618ms
264:	learn: 0.0926172	total: 2.1s	remaining: 611ms
265:	learn: 0.0924076	total: 2.11s	remaining: 603ms
266:	learn: 0.0920482	total: 2.12s	remaining: 594ms
267:	learn: 0.0917607	total: 2.12s	remaining: 587ms
268:	learn: 0.0912733	total: 2.13s	remaining: 579ms
269:	learn: 0.0909103	total: 2.14s	remaining: 570ms
270:	learn: 0.0905461	total: 2.15s	remaining: 562ms
271:	learn: 0.0903239	total: 2.15s	remaining: 554ms
272:	learn: 0

In [10]:
y_pred = catboost_mean_encoding.predict_proba(df_test_mean_encoding)[:,1]
submission_catboost = pd.DataFrame(data={'Opportunity_ID':df_test_mean_encoding['Opportunity_ID'], 'Target': y_pred})
submission_catboost = submission_catboost.groupby("Opportunity_ID").agg({"Target":"mean"}).reset_index()
submission_catboost.to_csv('../submits/mean_catboost.csv', index=False)